## LSST Solar System Processing

## Linking of Simulated dataset with HelioLinC3D

### Algorithm: 

* Similar to HelioLinC (Holman et al. 2018) we transform topocentric observations to heliocentric states assuming a distance and radial velocity.
* The resulting 3D positions are collected into tracklets. Tracklets contain at least two observations and can, thus, be used to create velocity vectors.
* A tracklet + velocity vector is called an "arrow". 
* Arrows are propagated to a common epoch using spiceypy's 2body propagator, and then clustered using dbscan.
* We calculate a mean state and variance for each cluster (trimmed mean), which is our best guess for the underlying orbit (IOD)
* We can filter all clusters based on their variance

### Implementation:
S. Eggl 20210218
    
### Last modified:
S. Eggl 20220627

In [1]:
# HelioLinC3D Solar System Processing functions for LSST
import heliolinc3d as hl

In [2]:
# Did I Find It analysis tool (Moeyens et al.)
import difi

In [3]:
from difi import __version__
print("difi version: {}".format(__version__))

difi version: 1.1


In [4]:
# Demo relevant python modules
import numpy as np
import pandas as pd
import os
import matplotlib.pyplot as plt
import plotly.express as px
import warnings
warnings.filterwarnings('ignore')

In [5]:
# Joblib prallelization
import joblib
from joblib.externals.loky import set_loky_pickler
from joblib import parallel_backend
from joblib import wrap_non_picklable_objects
from joblib import Parallel, delayed

In [6]:
# Progress bar for joblib processes
import contextlib
from tqdm import tqdm

@contextlib.contextmanager
def tqdm_joblib(tqdm_object):
    """Context manager to patch joblib to report into tqdm progress bar given as argument"""
    class TqdmBatchCompletionCallback:
        def __init__(self, time, index, parallel):
            self.index = index
            self.parallel = parallel

        def __call__(self, index):
            tqdm_object.update()
            if self.parallel._original_iterator is not None:
                self.parallel.dispatch_next()

    old_batch_callback = joblib.parallel.BatchCompletionCallBack
    joblib.parallel.BatchCompletionCallBack = TqdmBatchCompletionCallback
    try:
        yield tqdm_object
    finally:
        joblib.parallel.BatchCompletionCallBack = old_batch_callback
        tqdm_object.close()   

## SIMULATED OBSERVATIONS 


### Select observations from LSST Survey Simulation Dataset

Cornwall et al. 2021, 3deg x 3deg, 16 nights of baseline 1.7.1 LSST/Rubin Opsim + Synthetic Solar System Model (S3M)

In [7]:
# read in HDF5 database as pandas data frame
dfObs=pd.read_hdf('examples/data/S3M_LSST_test_observations.h5')

In [8]:
dfObs

ObjID  FieldID      FieldMJD  AstRange(km)  AstRangeRate(km/s)  \
0      S1005zBsa      322  59854.134964  3.903528e+08           18.438325   
1      S1000BHqa      323  59854.135412  1.335147e+08            9.922900   
2      S10032DHa      323  59854.135412  3.540569e+08           16.413993   
3      S100KUqra      323  59854.135412  2.009614e+08           17.690016   
4      S1005AL4a      323  59854.135412  3.323034e+08           17.218939   
...          ...      ...           ...           ...                 ...   
14202  S100pEx6a    12164  59869.998580  3.514039e+08           21.531036   
14203  S100MzuSa    12164  59869.998580  2.545696e+08           20.386812   
14204  S100JDrza    12164  59869.998580  3.222315e+08           22.449487   
14205  S1004VwEa    12164  59869.998580  3.672006e+08           23.023468   
14206  S100j6zBa    12164  59869.998580  3.212131e+08           16.304325   

       AstRA(deg)  AstRARate(deg/day)  AstDec(deg)  AstDecRate(deg/day)  \
0      317.007162           -0.012928    -5.883793            -0.034805   
1      317.230318            0.121660    -7.215994            -0.021378   
2      317.621096           -0.046593    -7.659217            -0.074332   
3      317.008627            0.068307    -7.344556            -0.051081   
4      317.067163           -0.008325    -7.480742            -0.087330   
...           ...                 ...          ...                  ...   
14202  317.190970            0.079577    -5.130440            -0.015811   
14203  317.101661            0.166477    -5.140825            -0.050978   
14204  317.083692            0.088453    -5.318370             0.032007   
14205  317.243144            0.070462    -5.068241            -0.000824   
14206  317.032211            0.063046    -5.273178            -0.046266   

       Ast-Sun(J2000x)(km)  ...         SNR  AstrometricSigma(deg)  \
0             4.320857e+08  ...   15.131873               0.000012   
1             2.453059e+08  ...  775.318617               0.000003   
2             4.072802e+08  ...   13.911700               0.000013   
3             2.938590e+08  ...    6.129057               0.000029   
4             3.892966e+08  ...   27.161090               0.000007   
...                    ...  ...         ...                    ...   
14202         3.926581e+08  ...    8.990583               0.000018   
14203         3.216310e+08  ...    5.215250               0.000030   
14204         3.708631e+08  ...    6.651233               0.000024   
14205         4.044528e+08  ...   13.797897               0.000012   
14206         3.699418e+08  ...   19.627342               0.000008   

       MaginFilter  dmagDetect  AstRATrue(deg)  AstDecTrue(deg)  filter  \
0        20.706603    0.000562      317.007156        -5.883805       y   
1        14.952667    0.006333      317.230318        -7.215994       y   
2        20.866671    0.003237      317.621091        -7.659233       y   
3        21.697419    0.003044      317.008629        -7.344537       y   
4        20.070287    0.003253      317.067154        -7.480754       y   
...            ...         ...             ...              ...     ...   
14202    23.400043    0.003453      317.190977        -5.130444       r   
14203    23.813880    0.015719      317.101637        -5.140838       r   
14204    23.744959    0.004636      317.083701        -5.318376       r   
14205    22.917715    0.002606      317.243159        -5.068255       r   
14206    22.376534    0.003215      317.032204        -5.273178       r   

       class  obsName  obsId  
0        MBA   956799      0  
1        MBA   832613      1  
2        MBA   859226      2  
3        MBA  7993708      3  
4        MBA   687450      4  
...      ...      ...    ...  
14202    MBA  6410097  14202  
14203    MBA  8257306  14203  
14204    MBA  8257947  14204  
14205    MBA  1202269  14205  
14206    MBA  5112601  14206  

[14207 rows x 37 columns]

In [9]:
# convert observations to HelioLinC ingestible format
dfHeliolincInput=hl.obs2heliolinc(dfObs);

In [10]:
# add observer states for observation epochs
dfHeliolincInput[['x_obs','y_obs','z_obs']], dfHeliolincInput[['vx_obs','vy_obs','vz_obs']] = hl.getObserverStates(dfHeliolincInput['time'],origin='SSB',observer_location='I11',ephemeris_dt='1h',frame='ecliptic')

In [11]:
dfHeliolincInput['night'] = hl.whichNight(dfHeliolincInput['time'])

In [12]:
dfHeliolincInput

obsName          time          RA       DEC  obsId     x_obs     y_obs  \
0       956799  59854.135765  317.007162 -5.883793      0  0.998881  0.148955   
1       832613  59854.136212  317.230318 -7.215994      1  0.998879  0.148963   
2       859226  59854.136212  317.621096 -7.659217      2  0.998879  0.148963   
3      7993708  59854.136212  317.008627 -7.344556      3  0.998879  0.148963   
4       687450  59854.136212  317.067163 -7.480742      4  0.998879  0.148963   
...        ...           ...         ...       ...    ...       ...       ...   
14202  6410097  59869.999381  317.190970 -5.130440  14202  0.917479  0.408951   
14203  8257306  59869.999381  317.101661 -5.140825  14203  0.917479  0.408951   
14204  8257947  59869.999381  317.083692 -5.318370  14204  0.917479  0.408951   
14205  1202269  59869.999381  317.243144 -5.068241  14205  0.917479  0.408951   
14206  5112601  59869.999381  317.032211 -5.273178  14206  0.917479  0.408951   

          z_obs    vx_obs    vy_obs    vz_obs  night  
0     -0.000232 -0.002816  0.017164 -0.000091  59854  
1     -0.000232 -0.002816  0.017164 -0.000091  59854  
2     -0.000232 -0.002816  0.017164 -0.000091  59854  
3     -0.000232 -0.002816  0.017164 -0.000091  59854  
4     -0.000232 -0.002816  0.017164 -0.000091  59854  
...         ...       ...       ...       ...    ...  
14202 -0.000243 -0.007184  0.015780 -0.000067  59870  
14203 -0.000243 -0.007184  0.015780 -0.000067  59870  
14204 -0.000243 -0.007184  0.015780 -0.000067  59870  
14205 -0.000243 -0.007184  0.015780 -0.000067  59870  
14206 -0.000243 -0.007184  0.015780 -0.000067  59870  

[14207 rows x 12 columns]

### Plot Observations with plotly express

In [13]:
# plot observation signal to noise ratio
fig = px.scatter(dfObs, x="AstRA(deg)", y="AstDec(deg)", color="class", size='SNR',size_max=30,
                 width=700, height=600)
fig.show()

### How many nights do we actually observe?

In [14]:
df_grouped_by_night=dfHeliolincInput.groupby('night')

In [15]:
len(df_grouped_by_night.groups)

10

In [16]:
df_grouped_by_night.groups.keys()

dict_keys([59854, 59855, 59860, 59861, 59862, 59863, 59865, 59867, 59869, 59870])

## How to run HelioLinC3D?

### Choose HelioLinC3D parameters

In [17]:
# Distance limit for tracklet (arrow) generation off of heliocentric positions from neighboring observations [au]
tracklet_construction_dmax = 0.016

# Clustering radius limit for propagated tracklets (arrows) [au]; propagated tracklets beyond this distance do not belong to the same cluster 
propagated_tracklet_dmax = 0.02

# Clusters are filtered by their compactness using the variance of the propagated and clustered tracklets wrt the mean state of clustered tracklets [au^2].
mean_state_variance_limit = 1e-6

# min temporal separation for tracklet generation from observations, e.g. exposure time (days)
t_sep_min=25/86400 

# max temporal separation for tracklet generation (days)
t_sep_max=1.5/24

# Minimum number of arrows to be considered a cluster ('DBSCAN input')
min_samples=3


In [18]:
# We do not consider trailed observations here.
dftrails = pd.DataFrame([])

### Run heliolinc in verbose mode for one set of r and rdot values

In [19]:
# heliocentric distance [au]
r_guess_1 = 3 
# heliocentric radial velocity [au/day]
rdot_guess_1 = 0

helres = hl.heliolinc3d(r_guess_1, rdot_guess_1, tracklet_construction_dmax, 
                       propagated_tracklet_dmax, t_sep_min, t_sep_max, 
                     dfobs=dfHeliolincInput, dftrails=dftrails,
                     min_samples=min_samples,
                     light_time=True, 
                     verbose=True, mean_state_variance_limit=mean_state_variance_limit) 
                     

obsids [[   16    42]
 [   34    42]
 [   29    42]
 ...
 [12825 13908]
 [12966 13416]
 [13202 13624]]
nobsarrows 10 596461
tarrow [59854.13621249 59854.13621249 59854.13621249 ... 59869.99531274
 59869.99531274 59869.99531274]
xarrow [[ 2.64532885 -1.37633242  0.32852574]
 [ 2.64484327 -1.37708373  0.32930419]
 [ 2.64492316 -1.37684603  0.32966062]
 ...
 [ 2.74218669 -1.15399814  0.38561698]
 [ 2.74095597 -1.15510133  0.39102598]
 [ 2.74198529 -1.15341588  0.3887782 ]]
varrow [[-0.20723048 -0.22613349  0.73206652]
 [ 0.05711595  0.18351805  0.31099106]
 [ 0.01338011  0.05335466  0.11576875]
 ...
 [ 0.00475608  0.01235069  0.00314606]
 [ 0.00370714  0.00915411  0.00105919]
 [ 0.00331164  0.00759598 -0.00081843]]
Number of arrows generated:  596461
Propagating arrows...
Propagated arrows xyz [[ 1.00123628 -3.16951187  6.13447659]
 [ 3.09705041  0.07873987  2.79558619]
 [ 2.75014699 -0.95325552  1.2476533 ]
 ...
 [ 2.70354183 -1.2515026   0.36054594]
 [ 2.71062614 -1.22726657  0.38249531

In [20]:
# HelioLinC3D results are returned in a pandas data frame
helres

clusterId                                              obsId  trailId  r  \
0            1                    [20, 73, 716, 1310, 2380, 2539]       -1  3   
1            2                          [34, 49, 710, 1315, 2408]       -1  3   
2            3                     [8, 45, 712, 1305, 2407, 2540]       -1  3   
3            5              [23, 41, 694, 1318, 1359, 2297, 2401]       -1  3   
4            6  [19, 50, 686, 1098, 1292, 2174, 2411, 2526, 27...       -1  3   
..         ...                                                ...      ... ..   
317      35564                       [11601, 11948, 12053, 12411]       -1  3   
318      35565                              [12004, 12054, 12480]       -1  3   
319      35569                       [11806, 12018, 12345, 12438]       -1  3   
320      35618         [10862, 11314, 11793, 12287, 12550, 12686]       -1  3   
321      35622                              [13222, 13474, 14075]       -1  3   

     drdt  cluster_epoch     x_ecl     y_ecl     z_ecl    vx_ecl    vy_ecl  \
0       0   59862.067573  2.685130 -1.303208  0.303473  0.004562  0.008874   
1       0   59862.067573  2.682706 -1.311325  0.290629  0.004744  0.008639   
2       0   59862.067573  2.682674 -1.298315  0.344842  0.004428  0.009807   
3       0   59862.067573  2.697151 -1.266165  0.357787  0.005945  0.012981   
4       0   59862.067573  2.689119 -1.290537  0.321997  0.004618  0.009555   
..    ...            ...       ...       ...       ...       ...       ...   
317     0   59862.067573  2.720312 -1.230322  0.298352  0.005752  0.013301   
318     0   59862.067573  2.719473 -1.223471  0.332510  0.005997  0.012387   
319     0   59862.067573  2.715578 -1.217491  0.384632  0.006808  0.015083   
320     0   59862.067573  2.711394 -1.218345  0.407863  0.005331  0.012437   
321     0   59862.067573  2.693891 -1.260650  0.388528  0.003334  0.006552   

       vz_ecl       var_pos       var_vel  
0   -0.002112  1.185061e-07  2.250968e-09  
1   -0.004368  4.138337e-08  7.642640e-10  
2    0.003010  2.625975e-07  3.934067e-09  
3    0.003423  3.522208e-07  5.246808e-09  
4   -0.000015  1.623578e-07  5.242711e-09  
..        ...           ...           ...  
317  0.000527  1.144900e-09  4.549935e-11  
318 -0.005255  4.809920e-07  1.904439e-08  
319 -0.002701  1.024030e-08  4.078248e-10  
320  0.000662  3.700481e-07  2.267209e-08  
321 -0.000962  3.659164e-07  5.839698e-09  

[322 rows x 14 columns]

In [21]:
# We can use the information stored in the test data set to see which S3M object is responsible for the observations that have been clustered by HelioLinC3D. 
# If only one designation appears in the cluster, the cluster is pure, i.e. only observations of one single object have been collected.
for index, row in helres.iterrows():
    print(dfObs[dfObs['obsId'].isin(helres["obsId"][index])].ObjID)

20      S100aNYna
73      S100aNYna
716     S100aNYna
1310    S100aNYna
2380    S100aNYna
2539    S100aNYna
Name: ObjID, dtype: object
34      S100axhFa
49      S100axhFa
710     S100axhFa
1315    S100axhFa
2408    S100axhFa
Name: ObjID, dtype: object
8       S1007Vb4a
45      S1007Vb4a
712     S1007Vb4a
1305    S1007Vb4a
2407    S1007Vb4a
2540    S1007Vb4a
Name: ObjID, dtype: object
23      S100d9mta
41      S100d9mta
694     S100d9mta
1318    S100d9mta
1359    S100d9mta
2297    S100d9mta
2401    S100d9mta
Name: ObjID, dtype: object
19      S1002qrHa
50      S1002qrHa
686     S1002qrHa
1098    S1002qrHa
1292    S1002qrHa
2174    S1002qrHa
2411    S1002qrHa
2526    S1002qrHa
2716    S1002qrHa
3593    S1002qrHa
5028    S1002qrHa
5529    S1002qrHa
Name: ObjID, dtype: object
28      S100dggda
53      S100dggda
288     S100dggda
674     S100dggda
1205    S100dggda
1295    S100dggda
1650    S100dggda
2405    S100dggda
2551    S100dggda
Name: ObjID, dtype: object
31       S100fLxqa
56       

2983    S1004FIxa
3944    S1004FIxa
5273    S1004FIxa
Name: ObjID, dtype: object
3008    S1002nJoa
3949    S1002nJoa
4368    S1002nJoa
5218    S1002nJoa
Name: ObjID, dtype: object
2853    S1003OfEa
3019    S1003OfEa
3659    S1003OfEa
3831    S100euela
4219    S100euela
4697    S100euela
Name: ObjID, dtype: object
2839    S1001aLta
2938    S1001aLta
3657    S1001aLta
3831    S100euela
4219    S100euela
4697    S100euela
Name: ObjID, dtype: object
2866    S1002DCma
3290    S1002DCma
3660    S1002DCma
3825    S1008pspa
4202    S1008pspa
4728    S1008pspa
Name: ObjID, dtype: object
2866    S1002DCma
3290    S1002DCma
3660    S1002DCma
3792    S1002DCma
4682    S1003OfEa
5309    S1003OfEa
Name: ObjID, dtype: object
2866    S1002DCma
3290    S1002DCma
3660    S1002DCma
3792    S1002DCma
4715    S1001aLta
5307    S1001aLta
Name: ObjID, dtype: object
2839    S1001aLta
2938    S1001aLta
3657    S1001aLta
3871    S1001aLta
4694    S1002DCma
5308    S1002DCma
Name: ObjID, dtype: object
2853    S1

### Heliocentric distance and radial velocity grid
The previous example was only using one guess for the heliocentric distance and radial velocity of solar system objects. Let us now conduct a grid search: 

In [22]:
# define range of heliocentric distances
r_guess=np.arange(2,4,0.2)
#rall=np.arange(6,30,2)
# define range of heliocentric radial velocities
rdot_guess=np.arange(-0.006,0.006,0.001)
np.append(rdot_guess,0.0)

# Iterator for joblib based paralellization
rrdot_grid=np.array(np.meshgrid(r_guess,rdot_guess)).T.reshape(-1,2)

# How many configuraitons do we have to run?
print(len(rrdot_grid))

120


In [ ]:
# Parallelize computation over a grid of initial conditions
n_cores=10

with tqdm_joblib(tqdm(desc="HelioLinC3D", total=len(rrdot_grid))) as progress_bar:
        clusters_df=Parallel(n_jobs=n_cores)(delayed(hl.heliolinc3d)
                                          (r, rdot, 
                                           tracklet_construction_dmax, 
                                           propagated_tracklet_dmax, 
                                           t_sep_min, t_sep_max, 
                                           dfobs=dfHeliolincInput,
                                           dftrails=dftrails,
                                           min_samples=min_samples,
                                           light_time=False, 
                                           verbose=False, 
                                           mean_state_variance_limit=mean_state_variance_limit) 
                                           for r, rdot in rrdot_grid ) 



HelioLinC3D:  16%|█▌        | 19/120 [05:31<13:32,  8.04s/it]  

## Resulting Linkages

In [ ]:
# Each set of initial conditions produces a data frame with suggested linkages; we merge all of them and give them a unique index
clustered_observations = (pd.concat(clusters_df)).reset_index(drop=True)  
clustered_observations['clusterId']=clustered_observations.index

In [ ]:
# deduplicate clusters with the same observations
dedupe=hl.deduplicateClusters(clustered_observations.sort_values(by=['var_pos','var_vel']) ).reset_index(drop=True)
dedupe['cluster_Id']=dedupe.index

In [ ]:
dedupe.head()

In [ ]:
# Number of clusters respresenting potential objects after deduplication
len(dedupe)

## Initial Orbit Determination included
The "mean state" given for each cluster corresponds to a complete set of positions and velocities at epoch that the propagated tracklets cluster around. Mean states make for excellent intial guesses for other orbit determination based filtering.

## Run DIFI
'Did I find it?' alias DIFI is a package that allows us to calculate key metrics relevant for LSST. For instance, we can see how many of the objects that are supposed to be findable with LSST required sets of pairs over three different nights during a 14 day linking window.

In [ ]:
# DIFI compares clusters and objects that were linked through HelioLinC3D to the best case scenario.
dfdifi=hl.linkages2difi(dedupe,clusterId_name='cluster_Id',observationId_name='obsId',output='pandas')
dfobs_difi=dfObs.merge(dfHeliolincInput,left_on='obsName',right_on='obsName')
dfobs_difi['obsId']=dfobs_difi['obsId_x'].astype(str)

(all_truths, findable_observations, summary, 
           all_linkages_heliolinc, all_truths_heliolinc, summary_heliolinc,
           findable_objects, missed_objects) = hl.runDifi(dfobs_difi, dedupe, 
                                                          obsIdName='obsId', linkageIdName='cluster_Id',
                                                          objIdName='ObjID', nightName='night', timeName='time',
                                                          findability='tracklet', linkage_min_obs=2, 
                                                          max_obs_separation=1.5/24, 
                                                          min_linkage_nights=3, 
                                                          metric="nightly_linkages")



In [ ]:
summary_heliolinc

We found 88 percent of all asteroids that should be findable with the LSST three nighters restrictions, but we also found about 70 more with observations that do not follow this pattern. 

In [ ]:
# purity of the found linkages [%], i.e. no observation of another object is polluting the cluster/linkage.
summary_heliolinc.pure_linkages/summary_heliolinc.linkages*100

In [ ]:
# The number of clusters containing potential objects is still high wrt to the number of actual objects in the data. 
len(dedupe)

## Mean State Filtering

In [ ]:
# Filtering clusters with respect to their internal dispersion will increase purity of the potential discoveries at the cost of lowering completeness.
variance_limit=1e-7
msf=dedupe[dedupe['var_pos']<variance_limit].reset_index(drop=True)  
msf['cluster_Id']=msf.index

In [ ]:
# number of resulting clusters
len(msf)

In [ ]:
dfdifi=hl.linkages2difi(msf,clusterId_name='cluster_Id',observationId_name='obsId',output='pandas')
dfobs_difi=dfObs.merge(dfHeliolincInput,left_on='obsName',right_on='obsName')
dfobs_difi['obsId']=dfobs_difi['obsId_x'].astype(str)

(all_truths, findable_observations, summary, 
           all_linkages_heliolinc, all_truths_heliolinc, summary_heliolinc,
           findable_objects, missed_objects) = hl.runDifi(dfobs_difi, msf, 
                                                          obsIdName='obsId', linkageIdName='cluster_Id',
                                                          objIdName='ObjID', nightName='night', timeName='time',
                                                          findability='tracklet', linkage_min_obs=2, 
                                                          max_obs_separation=1.5/24, 
                                                          min_linkage_nights=3, 
                                                          metric="nightly_linkages")

In [ ]:
# Now we have roughly as many clusters as there are objects to be discovered. However, the completenss took a hit.
summary_heliolinc

In [ ]:
# purity
summary_heliolinc.pure_linkages/summary_heliolinc.linkages*100